In [1]:
import os
os.getcwd()

'/Users/robertstillwell/GovernmentInformant/my_workspace/project_specific/dataset_mapping/ACS'

In [1]:
from concurrent.futures import ThreadPoolExecutor
from tqdm import tqdm
import concurrent.futures
from my_secrets import MySecrets
census_api_key = MySecrets().census
# -*- coding: utf-8 -*-
import pandas as pd
import numpy as np
from io import BytesIO
import re
from azure.storage.blob import BlobServiceClient, BlobClient, ContainerClient
import requests
import json
import os
from openpyxl.utils.dataframe import dataframe_to_rows
from openpyxl import Workbook
from datetime import date
import time
from datetime import datetime
from concurrent.futures import ThreadPoolExecutor
import threading
from io import BytesIO
from bs4 import BeautifulSoup
import io
import pickle

def save_obj_to_blob(object_name, container_name, blob_name, connection_string):
    # Serialize the object
    serialized_object = pickle.dumps(object_name)

    # Create a blob client using the blob name and container name
    blob_service_client = BlobServiceClient.from_connection_string(connection_string)
    blob_client = blob_service_client.get_blob_client(container=container_name, blob=blob_name)

    # Upload the serialized object to the blob
    blob_client.upload_blob(serialized_object, overwrite=True)

    return 'Object saved to blob successfully'

def read_obj_from_blob(container_name, blob_name, connection_string):
    # Create a blob client using the blob name and container name
    blob_service_client = BlobServiceClient.from_connection_string(connection_string)
    blob_client = blob_service_client.get_blob_client(container=container_name, blob=blob_name)

    # Download the serialized object from the blob
    blob_data = blob_client.download_blob()
    serialized_object = blob_data.content_as_bytes()

    # Deserialize the object
    deserialized_object = pickle.loads(serialized_object)

    return deserialized_object


def read_from_blob(container_name, blob_name, thing3=None):
    connection_string = find_blob_keys(thing3)
    blob_service_client = BlobServiceClient.from_connection_string(connection_string)
    blob_client = blob_service_client.get_blob_client(container=container_name, blob=blob_name)
    blob_data = blob_client.download_blob()
    return io.StringIO(blob_data.content_as_text())  # Convert bytes to a file-like string object

def read_metadata(blob_name, container_name=None, thing3=None):
    if container_name == None:
        container_name = 'metadata-depot'
    return read_from_blob(container_name, blob_name, thing3).read()

def save_to_blob(data,container_name, blob_name, thing3=None):
    connection_string = find_blob_keys(thing3)
    blob_service_client = BlobServiceClient.from_connection_string(connection_string)
    blob_client = blob_service_client.get_blob_client(container=container_name, blob=blob_name)
    blob_client.upload_blob(data, overwrite=True)

def save_metadata(data,blob_name,container_name=None,thing3=None):
    if container_name == None:
        container_name = 'metadata-depot'
    save_to_blob(data,container_name, blob_name, thing3)
    return blob_name
    
def write_csv(df,file_name,container_name,connection_string=None,index=None):

    # Define Azure Blob Storage details
    if index == None:
        index = False
    else:
        index = True
    save_to_blob(df.to_csv(index=index), container_name, file_name, connection_string)
    return file_name

def read_csv(container_name, blob_name, thing3=None):
    blob_data = read_from_blob(container_name, blob_name, thing3)
    csv_data = blob_data.read()
    df = pd.read_csv(io.StringIO(csv_data), dtype=str)
    return df


def write_excel_wb(wb_name, dataframes, ws_names=None):
    if isinstance(df, pd.DataFrame):
        dataframes = [dataframes]
    if ws_name == None:
        ws_names = [f'column_{i}' for i in range(len(dataframes))]
    elif isinstance(ws_names, str):
        ws_names = [ws_names] + [f'sheet_{i}' for i in range(len(dataframes)-1)]
    elif isinstance(ws_names, list):
        ws_names = ws_names + [f'sheet_{i}' for i in range(len(dataframes)-len(ws_names))]
        
    if wb_name[-5:] != '.xlsx':
        wb_name = wb_name + '.xlsx'
    wb = Workbook()
    for df, ws_name in zip(dataframes, ws_names):
        df = df.replace(np.nan, None, regex=True)
        df.reset_index(inplace=True, drop=True)
        for col in df.columns:
            df[col] = [json.dumps(x) if isinstance(x, dict) else x for x in df[col]]
            df[col] = [json.dumps(x) if isinstance(x, list) else x for x in df[col]]
        ws = wb.create_sheet(title=ws_name)
        for r in dataframe_to_rows(df, index=True, header=True):
            ws.append(r)
    wb.save(wb_name)
    
    # Save the workbook to a file-like object
    file_obj = BytesIO()
    wb.save(file_obj)
    file_obj.seek(0)
    
    blob_name = wb_name
    write_file(blob_name, file_obj.read())
    return 'done'

def delete_blob(blob):
    container_client.delete_blob(blob.name)

# Threadpool Examples

            # except KeyboardInterrupt:
            #     # Interrupt the operation on keystroke ESC
            #     break
# counter = 0
# with ThreadPoolExecutor(max_workers=20) as executor:
#     for blob in blobs:
#         counter += 1
#         print(blob.name, counter, end='\r')
#         executor.submit(delete_blob, blob)

acct = {'dev':'metadata-depot','silver':'acs-collection-metadata'}

def json_from_blob(container_name, file_name, thing3=None):
    json_data = read_from_blob(container_name, file_name, thing3)
    json_data = json_data.read()
    json_data = json.loads(json_data)
    return json_data

class ContactPoint:
    def __init__(self, fn, hasEmail):
        self.fn = fn
        self.hasEmail = hasEmail

    def items(self,keep=None,exclude=None):
        if keep != None and exclude != None:
            raise ValueError('Only one of keep or exclude can be specified.')
        if keep == None and exclude == None:
            data_dict = {key: getattr(self, key) for key in vars(self)}
        return data_dict
    def keys(self):
        return list(vars(self).keys())
    def values(self):
        return list(vars(self).values())

    def to_json(self):
        def serialize(obj):
            """JSON serializer for objects not serializable by default json code"""
            if isinstance(obj, (datetime, date)):
                return obj.isoformat()
            # Add more types if necessary (like Decimal, etc.)

            # For custom objects, convert them to a dictionary or a serializable format
            if hasattr(obj, 'items'):
                return obj.items()

            return obj.__dict__

        return json.dumps(self, default=serialize, indent=4)
    
class Distribution:
    def __init__(self, **kwargs):
        self.type = kwargs.get('@type', None)
        self.accessURL = kwargs.get('accessURL', None)
        self.description = kwargs.get('description', None)
        self.format = kwargs.get('format', None)
        self.mediaType = kwargs.get('mediaType', None)
        self.title = kwargs.get('title', None)
        if self.format == 'API':
            self.API_endpoint = kwargs.get('accessURL', None)
    def items(self,keep=None,exclude=None):
        if keep != None and exclude != None:
            raise ValueError('Only one of keep or exclude can be specified.')
        if keep == None and exclude == None:
            data_dict = {key: getattr(self, key) for key in vars(self)}
        return data_dict
    def keys(self):
        return list(vars(self).keys())
    def values(self):
        return list(vars(self).values())

    def to_json(self):
        def serialize(obj):
            """JSON serializer for objects not serializable by default json code"""
            if isinstance(obj, (datetime, date)):
                return obj.isoformat()
            # Add more types if necessary (like Decimal, etc.)

            # For custom objects, convert them to a dictionary or a serializable format
            if hasattr(obj, 'items'):
                return obj.items()

            return obj.__dict__

        return json.dumps(self, default=serialize, indent=4)

class Organization:
    def __init__(self, **kwargs):
        self.type = kwargs.get('@type', None)
        self.name = kwargs.get('name', None)
        sub_org = kwargs.get('subOrganizationOf', None)
        self.subOrganizationOf = Organization(**sub_org) if sub_org else None

    def items(self,keep=None,exclude=None):
        if keep != None and exclude != None:
            raise ValueError('Only one of keep or exclude can be specified.')
        if keep == None and exclude == None:
            data_dict = {key: getattr(self, key) for key in vars(self)}
        return data_dict
    def keys(self):
        return list(vars(self).keys())
    def values(self):
        return list(vars(self).values())

    def to_json(self):
        def serialize(obj):
            """JSON serializer for objects not serializable by default json code"""
            if isinstance(obj, (datetime, date)):
                return obj.isoformat()
            # Add more types if necessary (like Decimal, etc.)

            # For custom objects, convert them to a dictionary or a serializable format
            if hasattr(obj, 'items'):
                return obj.items()

            return obj.__dict__

        return json.dumps(self, default=serialize, indent=4)

class Dataset:
    def __init__(self, **kwargs):
        self.name = '-'.join(kwargs.get('c_dataset', []))
        self.type = kwargs.get('@type', None)
        self.id = kwargs.get('@id', None)
        v = kwargs.get('c_vintage', None)
        if isinstance(v, int):
            self.vintage = str(v)
        elif isinstance(v, str):
            self.vintage = v
        elif isinstance(v, float):
            self.vintage = str(int(v))
        else:
            self.vintage = v
        if self.vintage == None:
            self.vintage = 'Timeseries'
        self.dataset = '-'.join(kwargs.get('c_dataset', []))
        self.dataset_key = str(self.vintage) + '-' + self.dataset 
        self.dataset_ext = str(self.vintage) + '/' + '/'.join(kwargs.get('c_dataset', []))
        self.geographyLink = kwargs.get('c_geographyLink', None)
        self.variablesLink = kwargs.get('c_variablesLink', None)
        self.tagsLink = kwargs.get('c_tagsLink', None)
        self.examplesLink = kwargs.get('c_examplesLink', None)
        self.groupsLink = kwargs.get('c_groupsLink', None) if kwargs.get('c_groupsLink', None) else kwargs.get('c_groupLink', None)
        self.documentationLink = kwargs.get('c_documentationLink', None)
        self.isMicrodata = kwargs.get('c_isMicrodata', False)
        self.isCube = kwargs.get('c_isCube', False)
        self.isAvailable = kwargs.get('c_isAvailable', False)
        self.title = kwargs.get('title', None)
        self.source_name = self.title
        self.source_url = f'https://census.gov/program-surveys/{self.dataset.split("-")[0]}.html' 
        self.accessLevel = kwargs.get('accessLevel', None)
        self.bureauCode = kwargs.get('bureauCode', [])
        self.description = kwargs.get('description', None)
        self.distribution = [Distribution(**dist) for dist in kwargs.get('distribution', [])]
        self.api_endpoint = self.distribution[0].API_endpoint if self.distribution[0].API_endpoint else None
        self.contactPoint = ContactPoint(**kwargs.get('contactPoint', {}))
        self.identifier = kwargs.get('identifier', None)
        self.keyword = kwargs.get('keyword', [])
        self.license = kwargs.get('license', None)
        self.modified = kwargs.get('modified', None)
        self.programCode = kwargs.get('programCode', [])
        self.references = kwargs.get('references', [])
        self.api_key_param = 'key='+ kwargs.get('api_key_param', '44f49cb8386c3bff8b39bb922f4119f5acdcfc0c')
        self.publisher = Organization(**kwargs.get('publisher', {}))
        for kwarg in kwargs:
            if kwarg not in self.keys():
                setattr(self, kwarg, kwargs[kwarg])
        self.geography = {'level':{}}
            
    def update_geography_level(self, level):
        self.geography['level'].update(level)
        return self.geography['level']
            
    def items(self,keep=None,exclude=None):
        if keep != None and exclude != None:
            raise ValueError('Only one of keep or exclude can be specified.')
        if keep == None and exclude == None:
            data_dict = {key: getattr(self, key) for key in vars(self)}
        return data_dict
    def keys(self):
        return list(vars(self).keys())
    def values(self):
        return list(vars(self).values())

    def to_json(self):
        def serialize(obj):
            """JSON serializer for objects not serializable by default json code"""
            if isinstance(obj, (datetime, date)):
                return obj.isoformat()
            # Add more types if necessary (like Decimal, etc.)

            # For custom objects, convert them to a dictionary or a serializable format
            if hasattr(obj, 'items'):
                return obj.items()

            return obj.__dict__
        return json.dumps(self, default=serialize, indent=4)
    
    def enrich(self, categories=None):
        if isinstance(categories, str):
            categories = [categories]
        if categories == None:
            categories = ['geography','variables','tags','examples','groups']
        categories = [c for c in categories if c + 'Link' in self.keys()]
        for category in categories:
            link = getattr(self, category + 'Link')
            if link != None:
                data = requests.get(link).json()
                self.category = data
                setattr(self, category, data)

        return self
class Vintage:
    def __init__(self, name, datasets):
        
        self.geography = {'level':{},'code_map':{}}
        self.datasets = {dataset.name:dataset for dataset in datasets if dataset.vintage == name}
        self.name = name

        
    def update_geography_code_map(self, code_map):
        self.geography['code_map'].update(code_map)
        return self
    
    def update_geography_level(self, level):
        self.geography['level'].update(level)
        return self
    
    def items(self,keep=None,exclude=None):
        if keep != None and exclude != None:
            raise ValueError('Only one of keep or exclude can be specified.')
        if keep == None and exclude == None:
            data_dict = {key: getattr(self, key) for key in vars(self)}
        return data_dict
    def keys(self):
        return list(vars(self).keys())
    def values(self):
        return list(vars(self).values())

    def to_json(self):
        def serialize(obj):
            """JSON serializer for objects not serializable by default json code"""
            if isinstance(obj, (datetime, date)):
                return obj.isoformat()
            # Add more types if necessary (like Decimal, etc.)

            # For custom objects, convert them to a dictionary or a serializable format
            if hasattr(obj, 'items'):
                return obj.items()
            return obj.__dict__

        return json.dumps(self, default=serialize, indent=4)
class Catalog:
    def __init__(self, **kwargs):
        self.name = kwargs.get('name', None)
        self.url = kwargs.get('url', None)
        self.context = kwargs.get('@context', None)
        self.type = kwargs.get('@type', None)
        self.conformsTo = kwargs.get('conformsTo', None)
        self.describedBy = kwargs.get('describedBy', None)
        self.api_key_param = 'key='+ kwargs.get('api_key_param', '44f49cb8386c3bff8b39bb922f4119f5acdcfc0c')
        # self.vintage = {}
        datasets = [Dataset(**dataset) for dataset in kwargs.get('dataset', [])]

        self.vintage = {vint:Vintage(vint, datasets) for vint in set([dataset.vintage for dataset in datasets])} 
        self.geography = {'level':{},'code_map':{}}
        
        for dataset in datasets:
            vintage = dataset.vintage
            if vintage not in self.vintage:
                self.vintage[vintage] = Vintage(vintage, [])
            self.vintage[vintage].datasets[dataset.name] = dataset

    def update_geography_code_map(self, code_map):
        self.geography['code_map'].update(code_map)
        return self
    
    def update_geography_level(self, level):
        self.geography['level'].update(level)
        return self
    
    def items(self,keep=None,exclude=None):
        if keep != None and exclude != None:
            raise ValueError('Only one of keep or exclude can be specified.')
        if keep == None and exclude == None:
            data_dict = {key: getattr(self, key) for key in vars(self)}
        return data_dict
    def keys(self):
        return list(vars(self).keys())
    def values(self):
        return list(vars(self).values())
    
    def to_json(self):
        def serialize(obj):
            """JSON serializer for objects not serializable by default json code"""
            if isinstance(obj, (datetime, date)):
                return obj.isoformat()
            # Add more types if necessary (like Decimal, etc.)

            # For custom objects, convert them to a dictionary or a serializable format
            if hasattr(obj, 'items'):
                return obj.items()

            return obj.__dict__

        return json.dumps(self, default=serialize, indent=4)

def get_group_universe_dict(vintage):
    file_dictionary = {'2005':'https://www2.census.gov/acs2005/Chapter_6_acs_2005_tables_Sum_file_shells.xls',
                    '2006':'https://www2.census.gov/acs2006/merge_5_6_final.xls',
                    '2007':'https://www2.census.gov/acs2007_1yr/summaryfile/merge_5_6_final.xls',
                    '2008':'https://www2.census.gov/programs-surveys/acs/summary_file/2008/documentation/1_year/user_tools/merge_5_6.xls',
                    '2009':'https://www2.census.gov/programs-surveys/acs/summary_file/2009/documentation/1_year/user_tools/merge_5_6.xls',
                    '2010':'https://www2.census.gov/programs-surveys/acs/summary_file/2010/documentation/1_year/user_tools/Sequence_Number_and_Table_Number_Lookup.xls',
                    '2011':'https://www2.census.gov/programs-surveys/acs/summary_file/2011/documentation/1_year/user_tools/Sequence_Number_and_Table_Number_Lookup.xls',
                    '2012':'https://www2.census.gov/programs-surveys/acs/summary_file/2012/documentation/1_year/user_tools/Sequence_Number_and_Table_Number_Lookup.xls',
                    '2013':'https://www2.census.gov/programs-surveys/acs/summary_file/2013/documentation/user_tools/ACS2013_TableShells.xls',
                    '2014':'https://www2.census.gov/programs-surveys/acs/summary_file/2014/documentation/user_tools/ACS2014_Table_Shells.xlsx',
                    '2015':'https://www2.census.gov/programs-surveys/acs/summary_file/2015/documentation/user_tools/ACS2015_Table_Shells.xlsx',
                    '2016':'https://www2.census.gov/programs-surveys/acs/summary_file/2016/documentation/user_tools/ACS2016_Table_Shells.xlsx',
                    '2017':'https://www2.census.gov/programs-surveys/acs/summary_file/2017/documentation/user_tools/ACS2017_Table_Shells.xlsx',
                    '2018':'https://www2.census.gov/programs-surveys/acs/summary_file/2018/documentation/user_tools/ACS2018_Table_Shells.xlsx',
                    '2019':'https://www2.census.gov/programs-surveys/acs/summary_file/2019/documentation/user_tools/ACS2019_Table_Shells.xlsx',
                    '2020':'https://www2.census.gov/programs-surveys/acs/summary_file/2020/documentation/user_tools/ACS2020_Table_Shells.xlsx',
                    '2021':'https://www2.census.gov/programs-surveys/acs/summary_file/2021/sequence-based-SF/documentation/user_tools/ACS2021_Table_Shells.xlsx',
                    '2022':'https://www2.census.gov/programs-surveys/acs/summary_file/2022/table-based-SF/documentation/ACS2022_Table_Shells.xlsx'
                   }
    if isinstance(vintage, int):
        vintage = str(vintage)
    url = file_dictionary[vintage]
    content = requests.get(url).content

    if int(vintage) == 2005:
        table_id = 0
        stub = 2
        sheet = 0
    elif int(vintage) <= 2012:
        table_id = 1
        stub = 7
        sheet = 0
    elif int(vintage) == 2013:
        table_id = 0
        stub = 3
        sheet = 1
    elif int(vintage) <= 2022:
        table_id = 0
        stub = 3
        sheet = 0
    else:
        raise Exception('vintage not supported')
    df = pd.read_excel(BytesIO(content), sheet_name=sheet)
    df.columns = df.columns.str.replace('\n', '', regex=True)
    df.columns = df.columns.str.strip() 

    stub_col = df.columns[stub]
    id_col = df.columns[table_id]
    df = df.astype(str)
    df.dropna(subset=[stub_col], inplace=True)
    universe_dict = {}
    for i,row in df.iterrows():
        if pd.notnull(row[stub_col]):
            if 'Universe:' in row[stub_col]:
                universe = {row[id_col]:{row[stub_col].split(':')[0].strip():row[stub_col].split(':')[1].strip()}}
                universe_dict.update(universe)
    return universe_dict

def remove_special_characters(string):
    pattern = r"[,;:{}()\n\t=]"
    return re.sub(pattern, "", string)
# Create the catalog

class Group:
    def __init__(self,** kwargs):
        self.name = kwargs.get('name', None)
        self.description = kwargs.get('description', None)
        self.variables = {}
        self.variables['variableLink'] = kwargs.get('variables', None)
    
    def enrich(self):
        link = self.variables['variableLink']
        if link != None:
            try:
                data = requests.get(link).json()
                self.variables = data
                self.variables['variableLink'] = link
            except:
                return 'error - no variables link found'
        return self
    


    def items(self,keep=None,exclude=None):
        if keep != None and exclude != None:
            raise ValueError('Only one of keep or exclude can be specified.')
        if keep == None and exclude == None:
            data_dict = {key: getattr(self, key) for key in vars(self)}
        return data_dict
    def keys(self):
        return list(vars(self).keys())
    def values(self):
        return list(vars(self).values())

    def to_json(self):
        def serialize(obj):
            """JSON serializer for objects not serializable by default json code"""
            if isinstance(obj, (datetime, date)):
                return obj.isoformat()
            # Add more types if necessary (like Decimal, etc.)

            # For custom objects, convert them to a dictionary or a serializable format
            if hasattr(obj, 'items'):
                return obj.items()
            return obj.__dict__

        return json.dumps(self, default=serialize, indent=4)

def run_time_periods(dataset):
    if 'acs' in dataset.name:
        time_period = get_acs_period_type(dataset)
    elif 'cps' in dataset.name:
        time_period = get_cps_period_type(dataset)
    else:
        time_period = get_other_time_period(dataset)
    return time_period
def get_source_url(dataset):
    source_info = {'agency':dataset.publisher.name,
        'agency_url':'https://www.census.gov',
        'source':dataset.title,
        'source_url':dataset.source_url
    }
    return source_info

def get_acs_table_header(api_call_string):
    data = requests.get(api_call_string).json()
    header = data[0]
    ##### TODO ######
    # GET validation data from the API while getting headers to validate the data
    return header
def document_group(group):
    gname = group.name

    if not gname[1:3] == '25': #TODO need map for DP04
        return None
    try:
        national_schema = str(get_acs_table_header(f"{group.variables['variableLink'].split('/groups/')[0]}?get=group({group.name})&for=us:*&key={census_api_key}"))
    except:
        national_schema = None
        ###### TODO ###### add exceptions for the national table. x25 might not have them but others do. 
    # print(national_schema, end=', ')
    try:
        state_schema = str(get_acs_table_header(f"{group.variables['variableLink'].split('/groups/')[0]}?get=group({group.name})&for=state:53&key={census_api_key}"))
    except:
        state_schema = None
    # print(state_schema, end=', ')
    try:
        county_schema = str(get_acs_table_header(f"{group.variables['variableLink'].split('/groups/')[0]}?get=group({group.name})&for=county:033&in=state:53&key={census_api_key}"))
    except:
        county_schema = None
    # print(county_schema, end=', ')
    try:
        metro_schema = str(get_acs_table_header(f"{group.variables['variableLink'].split('/groups/')[0]}?get=group({group.name})&for=metropolitan%20statistical%20area/micropolitan%20statistical%20area:31100&key={census_api_key}"))
    except:
        metro_schema = None
    # print(metro_schema)

    mapper = {
        'name':dataset.name,
        'vintage':vintage.name,
        'group':group.name,
        'group_description': group.description,
        'metadata_link':group.variables['variableLink'],
        'metadata_bronze_schema':['metadata_url','vintage','collection','group','variable_name','variable_description','variable_label','variable_concept','variable_predicateType','variable_limit','variable_predicateOnly','variable_universe'],
        'national_link':f"{group.variables['variableLink'].split('/groups/')[0]}?get=group({group.name})&for=us:*",#&key=<census_api_key>"
        'national_bronze_schema':national_schema,
        'state_link': f"{group.variables['variableLink'].split('/groups/')[0]}?get=group({group.name})&for=state:*",#&key=<census_api_key>"
        'state_bronze_schema':state_schema,
        'county link' :f"{group.variables['variableLink'].split('/groups/')[0]}?get=group({group.name})&for=county:*",#&key=<census_api_key>"
        'county_bronze_schema':county_schema,
        'metro_link' : f"{group.variables['variableLink'].split('/groups/')[0]}?get=group({group.name})&for=metropolitan statistical area/micropolitan statistical area:*",#&key=<census_api_key>"
        'metro_bronze_schema':metro_schema
    }
    return mapper

In [ ]:

file_name = 'catalogs/census_api_data.json'
catalog_name = file_name.split('.')[0]
container_name = 'metadata-depot'
thing3 = 'dev'
url = 'https://api.census.gov/data.json'
response = requests.get(url)
data = json.loads(response.text)
data['name'] = catalog_name
catalog = Catalog(**data)
targetted_datasets = []
group_metadata_urls = []
n_vintages = len(catalog.vintage)


In [6]:

# targetted_datasets = []
for vintage_name, vintage in catalog.vintage.items():
    # if vintage_name == '2022':
    #     continue
    acs_datasets = [dataset for dataset in vintage.datasets.values() if 'acs' in dataset.name and 'pums' not in dataset.name]
    for dataset in acs_datasets:
        dataset.enrich('geography')
        dataset.enrich('groups')
        groups = [Group(**group) for group in dataset.groups['groups']]
        ###### FILTER FOR THE x25 GROUPS ######
        groups = [g for g in groups if g.name[1:3] == '25']
        with ThreadPoolExecutor(max_workers=20) as executor:
            futures = {executor.submit(document_group, group): group for group in groups}
            for future in tqdm(as_completed(futures), total=len(futures), desc="Processing Groups"):
                targetted_datasets.append(future.result())
targetted_datasets

Processing Groups: 100%|██████████| 150/150 [01:40<00:00,  1.50it/s]
Processing Groups: 0it [00:00, ?it/s]
Processing Groups: 0it [00:00, ?it/s]
Processing Groups: 0it [00:00, ?it/s]
Processing Groups: 100%|██████████| 6/6 [00:15<00:00,  2.59s/it]
Processing Groups: 0it [00:00, ?it/s]
Processing Groups: 100%|██████████| 164/164 [01:49<00:00,  1.50it/s]
Processing Groups: 0it [00:00, ?it/s]
Processing Groups: 0it [00:00, ?it/s]
Processing Groups: 0it [00:00, ?it/s]
Processing Groups: 100%|██████████| 6/6 [00:18<00:00,  3.16s/it]
Processing Groups: 0it [00:00, ?it/s]
Processing Groups: 100%|██████████| 196/196 [02:04<00:00,  1.58it/s]
Processing Groups: 0it [00:00, ?it/s]
Processing Groups: 0it [00:00, ?it/s]
Processing Groups: 0it [00:00, ?it/s]
Processing Groups: 100%|██████████| 150/150 [01:41<00:00,  1.48it/s]
Processing Groups: 0it [00:00, ?it/s]
Processing Groups: 0it [00:00, ?it/s]
Processing Groups: 0it [00:00, ?it/s]
Processing Groups: 100%|██████████| 196/196 [02:12<00:00,  1.4

[{'name': 'acs-acs1',
  'vintage': '2022',
  'group': 'B25096',
  'group_description': 'Mortgage Status by Value',
  'metadata_link': 'http://api.census.gov/data/2022/acs/acs1/groups/B25096.json',
  'metadata_bronze_schema': ['metadata_url',
   'vintage',
   'collection',
   'group',
   'variable_name',
   'variable_description',
   'variable_label',
   'variable_concept',
   'variable_predicateType',
   'variable_limit',
   'variable_predicate_Only',
   'variable_universe'],
  'national_link': 'http://api.census.gov/data/2022/acs/acs1?get=group(B25096)&for=us:*',
  'national_bronze_schema': "['B25096_001E', 'B25096_001EA', 'B25096_001M', 'B25096_001MA', 'B25096_002E', 'B25096_002EA', 'B25096_002M', 'B25096_002MA', 'B25096_003E', 'B25096_003EA', 'B25096_003M', 'B25096_003MA', 'B25096_004E', 'B25096_004EA', 'B25096_004M', 'B25096_004MA', 'B25096_005E', 'B25096_005EA', 'B25096_005M', 'B25096_005MA', 'B25096_006E', 'B25096_006EA', 'B25096_006M', 'B25096_006MA', 'B25096_007E', 'B25096_007E

In [7]:
df = pd.DataFrame(targetted_datasets)
df = df.sort_values(by=['name', 'group', 'vintage'])
df.reset_index(drop=True, inplace=True)
for col in df.columns:
    df[col] = [json.dumps(x) if isinstance(x, dict) else x for x in df[col]]
    df[col] = [json.dumps(x) if isinstance(x, list) else x for x in df[col]]
df['metadata_bronze_schema'] = ','.join(['metadata_url','vintage','collection','group','variable_name','variable_description','variable_label','variable_concept','variable_predicateType','variable_limit','variable_predicate_Only','variable_universe'])


wb = Workbook()
ws = wb.active
ws.title = 'x25_series_data.xlsx'
for r in dataframe_to_rows(df, index=True, header=True):
    ws.append(r)

save_path = f'V1 Work/ACS/{ws.title}'
os.makedirs(os.path.dirname(save_path), exist_ok=True)
if os.path.exists(save_path):
    os.remove(save_path)
wb.save(save_path)

In [ ]:
### TODO ### -- add a write to blob function at the end and then intgrate it into the code wehere headers are grabbed, why not just get all? 

meta_url = 'https://api.census.gov/data/2021/acs/acs1/groups/B25097.json'
data_url = 'https://api.census.gov/data/2021/acs/acs1?get=group(B25097)&for=county:*'
def convert_to_silver(data_url, meta_url=None):
    if not meta_url:
        return 'sorry - have not made that path yet.'
    data = get_data(data_url)
    headers = data[0]
    meta = get_meta(meta_url)
    metadata_headers = []
    for header in headers:
        print(header, end=' ')
        if header in meta.keys():
            print('is in the metadata keys', end=' ')
            mettta = meta[header]
            mettta['variable'] = header
            mettta['labels'] = mettta['label'].lower().split('!!') if 'label' in mettta.keys() else None
            if mettta['labels'] and mettta['label'] in ['Geography', 'Geographic Area Name']:
                mettta['concept'] = 'not applicable - source string simply listed all concepts'
                mettta['concepts'] = 'not applicable - source string simply listed all concepts'
            else:
                mettta['concepts'] = mettta['concept'].lower().split(' BY ') if 'concept' in mettta else None
            mettta['fact'] = mettta['concept'].split(' BY ')[0] if 'concept' in mettta else None
            
            metadata_headers.append(json.dumps(mettta))
            print('so we get a metadata json header, wahoo!')
        else:
            print('is not in the metadata keys')
            metadata_headers.append(header)
    return pd.DataFrame(data[1:], columns=metadata_headers)
df = convert_to_silver(data_url, meta_url)
df